In [29]:
from bs4 import BeautifulSoup

import pandas as pd #library for data analsysis 
import numpy as np # library to handle data in a vectorized manner

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

In [30]:
with open('Neighbourhoods.json') as f:
    data = json.load(f)

#df = pd.DataFrame.from_dict(json_normalize(data), orient='columns')    

#df.head()

area_num = []
area_name = []
lat = []
lng = []
for feature in data['features']:
    area_num.append(feature['properties']['AREA_SHORT_CODE'])
    area_name.append(feature['properties']['AREA_NAME'].rsplit("(",1)[0])
    lng.append(feature['properties']['LONGITUDE'])
    lat.append(feature['properties']['LATITUDE'])

df = pd.DataFrame ({"Neighbourhood Number":area_num, 
                    "Neighbourhood":area_name,
                    "Longitude":lng,
                    "Latitude":lat})

df.sort_values('Neighbourhood Number',ascending=True, inplace=True)
df.reset_index(drop=True, inplace=True)
df.head()

Neighbourhood Number                       Neighbourhood  Longitude  \
0                     1             West Humber-Clairville  -79.596356   
1                     2  Mount Olive-Silverstone-Jamestown  -79.587259   
2                     3       Thistletown-Beaumond Heights  -79.563491   
3                     4                    Rexdale-Kipling  -79.566228   
4                     5                   Elms-Old Rexdale  -79.548983   

    Latitude  
0  43.716180  
1  43.746868  
2  43.737988  
3  43.723725  
4  43.721519

Use geopy library to get the latitude and longitude values of Toronto.

In [31]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto, ON. are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto, ON. are 43.653963, -79.387207.


In [32]:
# create map of New York using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, num, hood in zip(df['Latitude'], df['Longitude'],df['Neighbourhood Number'], df['Neighbourhood']):
    label = '{}, {}'.format(num, hood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [33]:
toronto_geo = r'Neighbourhoods.json'

# create map and display it
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=12)
map_toronto.choropleth(
    geo_data=toronto_geo,
    data=df,
    columns=['Neighbourhood Number','Longitude'],
    key_on='feature.properties.AREA_LONG_CODE',
    fill_color='YlOrRd', 
    fill_opacity=0.6, 
    line_opacity=0.2,
    legend_name='Toronto Neighbourhood')
# display the map of Toronto
map_toronto

In [34]:
#read in the edited csv file
to_neighbourhood_edited = pd.read_csv("TOneighbourhoods_edited.csv", thousands=',') 

#drop the un-needed columns
to_neighbourhood_cleaned = to_neighbourhood_edited.drop(columns=['Category', 'Topic'])

#set the characteristic as index
to_neighbourhood_cleaned.set_index('Characteristic', inplace=True)

#drop the unnecessary rows before transpose
to_neighbourhood_cleaned.drop('TSNS2020 Designation',inplace=True)
to_neighbourhood_cleaned.drop('City of Toronto',axis=1,inplace=True)
#to_neighbourhood_cleaned.drop('Population Change 2011-2016',inplace=True)
                              
#transpose the dataframe so that rows will be the neighbourhoods                             
to_neighbourhood_cleaned = to_neighbourhood_cleaned.transpose()

#set the Neighbourhood Number as index
to_neighbourhood_cleaned.set_index('Neighbourhood Number')

#to_neighbourhood_cleaned.reset_index(drop=True,inplace=True)
#to_neighbourhood_cleaned.set_index('Neighbourhood Number', drop=True, inplace=True)

to_neighbourhood_cleaned['Population Change 2011-2016']=to_neighbourhood_cleaned['Population Change 2011-2016'].str.replace('%','')

to_neighbourhood_cleaned

Characteristic                    Neighbourhood Number Population, 2016  \
Agincourt North                                    129           29,113   
Agincourt South-Malvern West                       128           23,757   
Alderwood                                           20           12,054   
Annex                                               95           30,526   
Banbury-Don Mills                                   42           27,695   
Bathurst Manor                                      34           15,873   
Bay Street Corridor                                 76           25,797   
Bayview Village                                     52           21,396   
Bayview Woods-Steeles                               49           13,154   
Bedford Park-Nortown                                39           23,236   
Beechborough-Greenbrook                            112            6,577   
Bendale                                            127           29,960   
Birchcliffe-Cliffside                              122           22,291   
Black Creek                                         24           21,737   
Blake-Jones                                         69            7,727   
Briar Hill-Belgravia                               108           14,257   
Bridle Path-Sunnybrook-York Mills                   41            9,266   
Broadview North                                     57           11,499   
Brookhaven-Amesbury                                 30           17,757   
Cabbagetown-South St. James Town                    71           11,669   
Caledonia-Fairbank                                 109            9,955   
Casa Loma                                           96           10,968   
Centennial Scarborough                             133           13,362   
Church-Yonge Corridor                               75           31,340   
Clairlea-Birchmount                                120           26,984   
Clanton Park                                        33           16,472   
Cliffcrest                                         123           15,935   
Corso Italia-Davenport                              92           14,133   
Danforth                                            66            9,666   
Danforth East York                                  59           17,180   
...                                                ...              ...   
South Riverdale                                     70           27,876   
St.Andrew-Windfields                                40           17,812   
Steeles                                            116           24,623   
Stonegate-Queensway                                 16           25,051   
Tam O'Shanter-Sullivan                             118           27,446   
Taylor-Massey                                       61           15,683   
The Beaches                                         63           21,567   
Thistletown-Beaumond Heights                         3           10,360   
Thorncliffe Park                                    55           21,108   
Trinity-Bellwoods                                   81           16,556   
University                                          79            7,607   
Victoria Village                                    43           17,510   
Waterfront Communities-The Island                   77           65,913   
West Hill                                          136           27,392   
West Humber-Clairville                               1           33,312   
Westminster-Branson                                 35           26,274   
Weston                                             113           17,992   
Weston-Pelham Park                                  91           11,098   
Wexford/Maryvale                                   119           27,917   
Willowdale East                                     51           50,434   
Willowdale West                                     37           16,936   
Willowridge-Martingrove-R

In [35]:
to_neighbourhood_cleaned
to_neighbourhood_cleaned_num = pd.DataFrame()
to_neighbourhood_cleaned_num = to_neighbourhood_cleaned.apply(lambda x: pd.to_numeric(x.astype(str).str.replace(',',''), errors='coerce'))
to_neighbourhood_cleaned_num.dtypes



Characteristic
Neighbourhood Number                                                                                            int64
Population, 2016                                                                                                int64
Population Change 2011-2016                                                                                   float64
Total private dwellings                                                                                         int64
Population density per square kilometre                                                                         int64
Children (0-14 years)                                                                                           int64
Youth (15-24 years)                                                                                             int64
Working Age (25-54 years)                                                                                       int64
Pre-retirement (55-64 years)             

In [36]:
to_neighbourhood_cleaned_num.dropna(axis=1, how='any', thresh=None, subset=None, inplace=True)

In [37]:
to_neighbourhood_cleaned_num.sort_values('Neighbourhood Number', ascending=True, inplace=True)
to_neighbourhood_cleaned_num.reset_index(drop=True, inplace=True)

In [38]:
to_neighbourhood_cleaned_num.drop('Neighbourhood Number',axis=1,inplace=True)

In [39]:
to_neighbourhood_cleaned_num

Characteristic  Population, 2016  Population Change 2011-2016  \
0                          33312                         -2.3   
1                          32954                          0.5   
2                          10360                          2.2   
3                          10529                          0.4   
4                           9456                         -1.0   
5                          22000                          1.3   
6                          22156                          3.8   
7                          10948                          3.4   
8                          15535                          4.0   
9                          11051                         -1.3   
10                         18588                         -1.2   
11                         10554                          1.1   
12                         11848                          8.4   
13                         43965                         15.4   
14                          9271                          1.1   
15                         25051                          1.5   
16                         33964                         28.0   
17                         11463                          5.2   
18                         10084                          4.7   
19                         12054                          1.3   
20                         12416                         -0.9   
21                         15545                         -1.9   
22                         10722                         23.1   
23                         21737                         -1.5   
24                         30491                         -2.9   
25                         35052                          1.1   
26                         27593                         -0.4   
27                          9941                         -0.1   
28                         10111                         -0.8   
29                         17757                         -0.2   
..                           ...                          ...   
110                        22246                         -0.1   
111                         6577                          1.4   
112                        17992                         -1.0   
113                         7985                          0.8   
114                        13593                          3.4   
115                        24623                         -1.6   
116                        43993                         -2.1   
117                        27446                          0.2   
118                        27917                          3.3   
119                        26984                          8.9   
120                        13845                          2.6   
121                        22291                          2.0   
122                        15935                          1.5   
123                        17123                          0.4   
124                        13641                          4.2   
125                        25003                          2.6   
126                        29960                          7.5   
127                        23757                          8.0   
128                        29113                         -3.9   
129                        26572                         -2.2   
130                        46496                          1.3   
131                        43794                         -2.9   
132                        13362                          2.1   
133                        12494                         -4.6   
134                        17455                         -0.8   
135                        27392                          3.2   
136                        53485                          0.3   
137                        22776                         -0.2   
138                        16724                          0.7   
139                         9917   

In [46]:

df_combined = pd.DataFrame()
df_combined = pd.concat([df,to_neighbourhood_cleaned_num[['Population, 2016']]], axis=1)

df_combined

Neighbourhood Number                         Neighbourhood  Longitude  \
0                       1               West Humber-Clairville  -79.596356   
1                       2    Mount Olive-Silverstone-Jamestown  -79.587259   
2                       3         Thistletown-Beaumond Heights  -79.563491   
3                       4                      Rexdale-Kipling  -79.566228   
4                       5                     Elms-Old Rexdale  -79.548983   
5                       6        Kingsview Village-The Westway  -79.547863   
6                       7     Willowridge-Martingrove-Richview  -79.554221   
7                       8             Humber Heights-Westmount  -79.522416   
8                       9             Edenbridge-Humber Valley  -79.522458   
9                      10                   Princess-Rosethorn  -79.544559   
10                     11       Eringate-Centennial-West Deane  -79.580445   
11                     12                        Markland Wood  -79.573432   
12                     13                  Etobicoke West Mall  -79.568939   
13                     14           Islington-City Centre West  -79.543317   
14                     15                       Kingsway South  -79.510577   
15                     16                  Stonegate-Queensway  -79.501128   
16                     17  Mimico (includes Humber Bay Shores)  -79.500137   
17                     18                          New Toronto  -79.510358   
18                     19                          Long Branch  -79.533345   
19                     20                            Alderwood  -79.541611   
20                     21                        Humber Summit  -79.556175   
21                     22                           Humbermede  -79.542367   
22                     23                 Pelmo Park-Humberlea  -79.528282   
23                     24                          Black Creek  -79.521979   
24                     25               Glenfield-Jane Heights  -79.513465   
25                     26                 Downsview-Roding-CFB  -79.490497   
26                     27              York University Heights  -79.488883   
27                     28                               Rustic  -79.498091   
28                     29                           Maple Leaf  -79.480758   
29                     30                  Brookhaven-Amesbury  -79.485589   
..                    ...                                   ...        ...   
110                   111                    Rockcliffe-Smythe  -79.494420   
111                   112              Beechborough-Greenbrook  -79.479473   
112                   113                               Weston  -79.515723   
113                   114                   Lambton Baby Point  -79.496045   
114                   115                         Mount Dennis  -79.499989   
115                   116                              Steeles  -79.321207   
116                   117                           L'Amoreaux  -79.314084   
117                   118               Tam O'Shanter-Sullivan  -79.302919   
118                   119                     Wexford/Maryvale  -79.298637   
119                   120                  Clairlea-Birchmount  -79.281382   
120                   121                             Oakridge  -79.279708   
121                   122                Birchcliffe-Cliffside  -79.265093   
122                   123                           Cliffcrest  -79.235530   
123                   124                         Kennedy Park  -79.260382   
124                   125                              Ionview  -79.272470   
125                   126                          Dorset Park  -79.278908   
126                   127                              Bendale  -79.257400   
127                   128         Agincourt South-Malvern West  -79.265612   
128                   129                      Agincourt North  -79.266712   
129                   130  

In [47]:
toronto_geo = r'Neighbourhoods.json'

# create map and display it
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=12)
map_toronto.choropleth(
    geo_data=toronto_geo,
    data=df_combined,
    columns=['Neighbourhood Number','Population, 2016'],
    key_on='feature.properties.AREA_LONG_CODE',
    fill_color='YlOrRd', 
    fill_opacity=0.6, 
    line_opacity=0.2,
    legend_name='Toronto Neighbourhood')
# display the map of Toronto
map_toronto

## Normalize Data 

In [40]:
from sklearn import preprocessing


to_neighbourhood_cleaned_normalized = preprocessing.StandardScaler().fit(to_neighbourhood_cleaned_num.reset_index(drop=True)).transform(to_neighbourhood_cleaned_num.reset_index(drop=True))





/Users/dzl/anaconda3/lib/python3.7/site-packages/sklearn/preprocessing/data.py:645: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  return self.partial_fit(X, y)
/Users/dzl/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  after removing the cwd from sys.path.


In [41]:
to_neighbourhood_cleaned_normalized

array([[ 1.38039662, -0.7147478 ,  0.49110967, ...,  0.91949128,
        -0.56564436, -0.39390282],
       [ 1.34458836, -0.39912187,  0.3366529 , ...,  0.25184704,
        -0.63166062, -0.57695407],
       [-0.91533352, -0.20749184, -0.92670985, ..., -0.95596541,
        -0.53205029, -0.6893875 ],
       ...,
       [ 0.32655327, -0.47802836, -0.04171937, ..., -0.11682464,
        -0.59116544, -0.5882524 ],
       [-0.27878652, -0.37657716, -0.42851656, ..., -0.6799202 ,
        -0.45418496, -0.59280839],
       [-0.95964375, -0.3427601 , -0.81961982, ..., -0.68358857,
        -0.26290709, -0.48130449]])

## Finding Clusters

Using K-Means

In [42]:
# set number of clusters
kclusters = 8

to_neighbourhood_clustering = to_neighbourhood_cleaned_normalized

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(to_neighbourhood_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 7, 7, 7, 0, 4, 7, 1, 1], dtype=int32)

In [43]:
df['Cluster']=kmeans.labels_


In [44]:
df

Neighbourhood Number                         Neighbourhood  Longitude  \
0                       1               West Humber-Clairville  -79.596356   
1                       2    Mount Olive-Silverstone-Jamestown  -79.587259   
2                       3         Thistletown-Beaumond Heights  -79.563491   
3                       4                      Rexdale-Kipling  -79.566228   
4                       5                     Elms-Old Rexdale  -79.548983   
5                       6        Kingsview Village-The Westway  -79.547863   
6                       7     Willowridge-Martingrove-Richview  -79.554221   
7                       8             Humber Heights-Westmount  -79.522416   
8                       9             Edenbridge-Humber Valley  -79.522458   
9                      10                   Princess-Rosethorn  -79.544559   
10                     11       Eringate-Centennial-West Deane  -79.580445   
11                     12                        Markland Wood  -79.573432   
12                     13                  Etobicoke West Mall  -79.568939   
13                     14           Islington-City Centre West  -79.543317   
14                     15                       Kingsway South  -79.510577   
15                     16                  Stonegate-Queensway  -79.501128   
16                     17  Mimico (includes Humber Bay Shores)  -79.500137   
17                     18                          New Toronto  -79.510358   
18                     19                          Long Branch  -79.533345   
19                     20                            Alderwood  -79.541611   
20                     21                        Humber Summit  -79.556175   
21                     22                           Humbermede  -79.542367   
22                     23                 Pelmo Park-Humberlea  -79.528282   
23                     24                          Black Creek  -79.521979   
24                     25               Glenfield-Jane Heights  -79.513465   
25                     26                 Downsview-Roding-CFB  -79.490497   
26                     27              York University Heights  -79.488883   
27                     28                               Rustic  -79.498091   
28                     29                           Maple Leaf  -79.480758   
29                     30                  Brookhaven-Amesbury  -79.485589   
..                    ...                                   ...        ...   
110                   111                    Rockcliffe-Smythe  -79.494420   
111                   112              Beechborough-Greenbrook  -79.479473   
112                   113                               Weston  -79.515723   
113                   114                   Lambton Baby Point  -79.496045   
114                   115                         Mount Dennis  -79.499989   
115                   116                              Steeles  -79.321207   
116                   117                           L'Amoreaux  -79.314084   
117                   118               Tam O'Shanter-Sullivan  -79.302919   
118                   119                     Wexford/Maryvale  -79.298637   
119                   120                  Clairlea-Birchmount  -79.281382   
120                   121                             Oakridge  -79.279708   
121                   122                Birchcliffe-Cliffside  -79.265093   
122                   123                           Cliffcrest  -79.235530   
123                   124                         Kennedy Park  -79.260382   
124                   125                              Ionview  -79.272470   
125                   126                          Dorset Park  -79.278908   
126                   127                              Bendale  -79.257400   
127                   128         Agincourt South-Malvern West  -79.265612   
128                   129                      Agincourt North  -79.266712   
129                   130  

In [45]:
# create map
map_clusters = folium.Map(location=[latitude+0.05, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df['Latitude'], df['Longitude'], df['Neighbourhood'], df['Cluster']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster+1), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [47]:
df_combined = pd.DataFrame()
df_combined = pd.concat([df[['Neighbourhood Number','Neighbourhood','Cluster']],
                         to_neighbourhood_cleaned_num[['Population, 2016',
                                                         'Average after-tax income of households in 2015 ($)',
                                                         '  Non-immigrants',
                                                         '  Immigrants',
                                                         '  Total visible minority population',
                                                         '  Not a visible minority',
                                                         '  Owner',
                                                         '  Renter',
                                                         '  Condominium',
                                                         '  Not condominium',
                                                         'Employment rate',
                                                         'Unemployment rate',
                                                         '  Car, truck, van - as a driver',
                                                         '  Car, truck, van - as a passenger',
                                                         '  Public transit',
                                                         '  Walked',
                                                         '  Bicycle']]], axis=1)
df_combined



Neighbourhood Number                         Neighbourhood  Cluster  \
0                       1               West Humber-Clairville         0   
1                       2    Mount Olive-Silverstone-Jamestown         0   
2                       3         Thistletown-Beaumond Heights         7   
3                       4                      Rexdale-Kipling         7   
4                       5                     Elms-Old Rexdale         7   
5                       6        Kingsview Village-The Westway         0   
6                       7     Willowridge-Martingrove-Richview         4   
7                       8             Humber Heights-Westmount         7   
8                       9             Edenbridge-Humber Valley         1   
9                      10                   Princess-Rosethorn         1   
10                     11       Eringate-Centennial-West Deane         4   
11                     12                        Markland Wood         1   
12                     13                  Etobicoke West Mall         7   
13                     14           Islington-City Centre West         3   
14                     15                       Kingsway South         1   
15                     16                  Stonegate-Queensway         4   
16                     17  Mimico (includes Humber Bay Shores)         2   
17                     18                          New Toronto         7   
18                     19                          Long Branch         1   
19                     20                            Alderwood         1   
20                     21                        Humber Summit         7   
21                     22                           Humbermede         7   
22                     23                 Pelmo Park-Humberlea         7   
23                     24                          Black Creek         0   
24                     25               Glenfield-Jane Heights         0   
25                     26                 Downsview-Roding-CFB         0   
26                     27              York University Heights         0   
27                     28                               Rustic         7   
28                     29                           Maple Leaf         7   
29                     30                  Brookhaven-Amesbury         7   
..                    ...                                   ...      ...   
110                   111                    Rockcliffe-Smythe         0   
111                   112              Beechborough-Greenbrook         7   
112                   113                               Weston         7   
113                   114                   Lambton Baby Point         1   
114                   115                         Mount Dennis         7   
115                   116                              Steeles         0   
116                   117                           L'Amoreaux         3   
117                   118               Tam O'Shanter-Sullivan         0   
118                   119                     Wexford/Maryvale         0   
119                   120                  Clairlea-Birchmount         0   
120                   121                             Oakridge         7   
121                   122                Birchcliffe-Cliffside         4   
122                   123                           Cliffcrest         7   
123                   124                         Kennedy Park         7   
124                   125                              Ionview         7   
125                   126                          Dorset Park         0   
126                   127                              Bendale         0   
127                   128         Agincourt South-Malvern West         0   
128                   129                      Agincourt North         0   
129                   130                             Milliken         0   
130                   131                            

Cluster 1

In [48]:
df_combined.loc[df_combined['Cluster'] == 0, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number                       Neighbourhood  Cluster  \
0                       1             West Humber-Clairville         0   
1                       2  Mount Olive-Silverstone-Jamestown         0   
5                       6      Kingsview Village-The Westway         0   
23                     24                        Black Creek         0   
24                     25             Glenfield-Jane Heights         0   
25                     26               Downsview-Roding-CFB         0   
26                     27            York University Heights         0   
34                     35                Westminster-Branson         0   
35                     36                   Newtonbrook West         0   
43                     44                    Flemingdon Park         0   
46                     47                 Don Valley Village         0   
54                     55                   Thorncliffe Park         0   
110                   111                  Rockcliffe-Smythe         0   
115                   116                            Steeles         0   
117                   118             Tam O'Shanter-Sullivan         0   
118                   119                   Wexford/Maryvale         0   
119                   120                Clairlea-Birchmount         0   
125                   126                        Dorset Park         0   
126                   127                            Bendale         0   
127                   128       Agincourt South-Malvern West         0   
128                   129                    Agincourt North         0   
129                   130                           Milliken         0   
135                   136                          West Hill         0   
137                   138                      Eglinton East         0   

     Population, 2016  Average after-tax income of households in 2015 ($)  \
0               33312                                             426156    
1               32954                                             360648    
5               22000                                             272950    
23              21737                                             261560    
24              30491                                             410012    
25              35052                                             562794    
26              27593                                             302358    
34              26274                                             332776    
35              23831                                             260415    
43              21933                                             261233    
46              27051                                             414411    
54              21108                                             195114    
110             22246                                             295358    
115             24623                                             363045    
117             27446                                             475647    
118             27917                                             336503    
119             26984                                             350777    
125             25003                                             251476    
126             29960                                             326482    
127             23757                                             278390    
128             29113                                             427037    
129             26572                                             525507    
135             27392                                             316750    
137             22776                                             343031    

       Non-immigrants    Immigrants    Total visible minority population  \
0               12285         19230                                26945   
1               10425         21500                                28455   


Cluster 2

In [49]:
df_combined.loc[df_combined['Cluster'] == 1, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number                       Neighbourhood  Cluster  \
8                       9           Edenbridge-Humber Valley         1   
9                      10                 Princess-Rosethorn         1   
11                     12                      Markland Wood         1   
14                     15                     Kingsway South         1   
18                     19                        Long Branch         1   
19                     20                          Alderwood         1   
37                     38                   Lansing-Westgate         1   
39                     40               St.Andrew-Windfields         1   
40                     41  Bridle Path-Sunnybrook-York Mills         1   
55                     56                 Leaside-Bennington         1   
57                     58                      Old East York         1   
58                     59                 Danforth East York         1   
59                     60                   Woodbine-Lumsden         1   
63                     64                  Woodbine Corridor         1   
64                     65                  Greenwood-Coxwell         1   
65                     66                           Danforth         1   
66                     67           Playter Estates-Danforth         1   
67                     68                    North Riverdale         1   
68                     69                        Blake-Jones         1   
70                     71    Cabbagetown-South St.James Town         1   
78                     79                         University         1   
79                     80            Palmerston-Little Italy         1   
80                     81                  Trinity-Bellwoods         1   
82                     83                     Dufferin Grove         1   
83                     84                    Little Portugal         1   
85                     86                       Roncesvalles         1   
88                     89       Runnymede-Bloor West Village         1   
89                     90                      Junction Area         1   
93                     94                           Wychwood         1   
95                     96                          Casa Loma         1   
96                     97                     Yonge-St.Clair         1   
98                     99                Mount Pleasant East         1   
99                    100                     Yonge-Eglinton         1   
100                   101                  Forest Hill South         1   
101                   102                  Forest Hill North         1   
102                   103                Lawrence Park South         1   
104                   105                Lawrence Park North         1   
105                   106                 Humewood-Cedarvale         1   
113                   114                 Lambton Baby Point         1   
132                   133             Centennial Scarborough         1   
139                   140                          Guildwood         1   

     Population, 2016  Average after-tax income of households in 2015 ($)  \
8               15535                                             441052    
9               11051                                             538736    
11              10554                                             195412    
14               9271                                             900624    
18              10084                                             137480    
19              12054                                             168602    
37              16164                                             356122    
39              17812                                             649291    
40               9266                                            1392010    
55              16828                                             841619    
57               9233                            

Cluster 3

In [50]:
df_combined.loc[df_combined['Cluster'] == 2, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number                         Neighbourhood  Cluster  \
16                     17  Mimico (includes Humber Bay Shores)         2   
74                     75                Church-Yonge Corridor         2   
75                     76                  Bay Street Corridor         2   
81                     82                              Niagara         2   
92                     93  Dovercourt-Wallace Emerson-Junction         2   
94                     95                                Annex         2   
103                   104                  Mount Pleasant West         2   

     Population, 2016  Average after-tax income of households in 2015 ($)  \
16              33964                                             583422    
74              31340                                             443734    
75              25797                                             352218    
81              31180                                             369683    
92              36625                                             594477    
94              30526                                             792507    
103             29658                                             443047    

       Non-immigrants    Immigrants    Total visible minority population  \
16              18925         13425                                10395   
74              16650         10935                                12440   
75               9995         10455                                15925   
81              20255          8995                                10665   
92              20635         14395                                12275   
94              19030          8270                                 7270   
103             15955         11295                                 9730   

       Not a visible minority    Owner    Renter    Condominium  \
16                      22915     9150      8635           9360   
74                      17880     5800     13865           9935   
75                       9675     4835     10245          10745   
81                      19765     9380      9395          15710   
92                      23935     7630      7665           1850   
94                      21380     6060      9870           4510   
103                     19200     4415     13070           5005   

       Not condominium  Employment rate  Unemployment rate  \
16                8430             66.6                6.2   
74                9745             68.7                8.5   
75                4330             56.2               10.2   
81                3070             82.7                4.5   
92               13455             65.2                7.2   
94               11430             65.8                6.7   
103              12490             69.5                6.7   

       Car, truck, van - as a driver    Car, truck, van - as a passenger  \
16                             11095                                 760   
74                              2705                                 245   
75                              1780                                 165   
81                              6820                                 640   
92                              5825                                 820   
94                              3290                                 290   
103                             4745                                 370   

       Public transit    Walked    Bicycle  
16               5040       505        310  
74               7000      7275        690  
75               3540      5840        325  
81               6965      5070       1330  
92               8950      1215       1980  
94               6200      3200       1675  
103              9435      1840        250

Cluster 4

In [51]:
df_combined.loc[df_combined['Cluster'] == 3, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number                Neighbourhood  Cluster  \
13                     14  Islington-City Centre West         3   
44                     45           Parkwoods-Donalda         3   
116                   117                  L'Amoreaux         3   
130                   131                       Rouge         3   
131                   132                     Malvern         3   
136                   137                      Woburn         3   

     Population, 2016  Average after-tax income of households in 2015 ($)  \
13              43965                                             854623    
44              34805                                             623453    
116             43993                                             529383    
130             46496                                             729154    
131             43794                                             533202    
136             53485                                             629030    

       Non-immigrants    Immigrants    Total visible minority population  \
13              22450         19590                                16035   
44              16630         17210                                19075   
116             13710         28325                                33540   
130             20025         25575                                37315   
131             15960         26900                                39195   
136             20645         30185                                40510   

       Not a visible minority    Owner    Renter    Condominium  \
13                      27195    11215      8105           8340   
44                      15655     5300      8020           1505   
116                      9945     9825      5205           4835   
130                      8750    11195      2205           1265   
131                      4580     9395      4020           4395   
136                     12495     9765      8670           3460   

       Not condominium  Employment rate  Unemployment rate  \
13               10980             63.6                7.3   
44               11800             57.3                9.2   
116              10205             50.4               10.9   
130              12125             59.4                8.2   
131               9020             55.5               10.5   
136              14980             51.9               10.6   

       Car, truck, van - as a driver    Car, truck, van - as a passenger  \
13                             11775                                 975   
44                              8580                                 820   
116                            10005                                1220   
130                            13665                                1510   
131                            10785                                1400   
136                            11505                                1405   

       Public transit    Walked    Bicycle  
13               8205       795         90  
44               5275       420         45  
116              5895       370         85  
130              5935       220         20  
131              6425       425         60  
136              7635       780         45

Cluster 5

In [52]:
df_combined.loc[df_combined['Cluster'] == 4, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number                      Neighbourhood  Cluster  \
6                       7  Willowridge-Martingrove-Richview         4   
10                     11    Eringate-Centennial-West Deane         4   
15                     16               Stonegate-Queensway         4   
31                     32               Englemount-Lawrence         4   
38                     39              Bedford Park-Nortown         4   
41                     42                 Banbury-Don Mills         4   
51                     52                   Bayview Village         4   
61                     62                 East End-Danforth         4   
62                     63                       The Beaches         4   
69                     70                   South Riverdale         4   
72                     73                         Moss Park         4   
84                     85                    South Parkdale         4   
86                     87                 High Park-Swansea         4   
87                     88                   High Park North         4   
97                     98               Rosedale-Moore Park         4   
106                   107                   Oakwood Village         4   
121                   122             Birchcliffe-Cliffside         4   

     Population, 2016  Average after-tax income of households in 2015 ($)  \
6               22156                                             412302    
10              18588                                             352269    
15              25051                                             516575    
31              22372                                             293189    
38              23236                                             720203    
41              27695                                             493486    
51              21396                                             354894    
61              21381                                             304010    
62              21567                                             659192    
69              27876                                             662651    
72              20506                                             170813    
84              21849                                             258500    
86              23925                                             483620    
87              22162                                             496958    
97              20923                                            1413132    
106             21210                                             267062    
121             22291                                             369161    

       Non-immigrants    Immigrants    Total visible minority population  \
6               11775         10030                                 8870   
10              10180          8190                                 5130   
15              15905          8635                                 4595   
31              11490          9785                                 8855   
38              15885          6805                                 4845   
41              13310         13195                                12700   
51               7220         12625                                14505   
61              14820          5920                                 6475   
62              16900          4225                                 2980   
69              18260          8210                                11225   
72              11240          6470                                 7860   
84              11025          8920                                 9920   
86              16315          6565                                 4465   
87              13340          7670                                 5185   
97              14490          5495                                 3740   
106             10280          9965                                 9045   
121        

Cluster 6

In [53]:
df_combined.loc[df_combined['Cluster'] == 5, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number     Neighbourhood  Cluster  Population, 2016  \
50                    51  Willowdale East         5             50434   

    Average after-tax income of households in 2015 ($)    Non-immigrants  \
50                                             572155              14150   

      Immigrants    Total visible minority population  \
50         31040                                37715   

      Not a visible minority    Owner    Renter    Condominium  \
50                     12545    13800      8505          16330   

      Not condominium  Employment rate  Unemployment rate  \
50               5970             55.9                8.5   

      Car, truck, van - as a driver    Car, truck, van - as a passenger  \
50                             9890                                 695   

      Public transit    Walked    Bicycle  
50              9390      1550         50

Cluster 7

In [54]:
df_combined.loc[df_combined['Cluster'] == 6, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number                       Neighbourhood  Cluster  \
76                    77  Waterfront Communities-The Island         6   

    Population, 2016  Average after-tax income of households in 2015 ($)  \
76             65913                                             662333    

      Non-immigrants    Immigrants    Total visible minority population  \
76             37035         23820                                28895   

      Not a visible minority    Owner    Renter    Condominium  \
76                     36715    16825     23930          35730   

      Not condominium  Employment rate  Unemployment rate  \
76               5030             78.2                5.2   

      Car, truck, van - as a driver    Car, truck, van - as a passenger  \
76                             9100                                 760   

      Public transit    Walked    Bicycle  
76             10915     20855       1570

Cluster 8

In [55]:
df_combined.loc[df_combined['Cluster'] == 7, df_combined.columns[list(range(0, df_combined.shape[1]))]]


Neighbourhood Number                  Neighbourhood  Cluster  \
2                       3  Thistletown-Beaumond Heights         7   
3                       4               Rexdale-Kipling         7   
4                       5              Elms-Old Rexdale         7   
7                       8      Humber Heights-Westmount         7   
12                     13           Etobicoke West Mall         7   
17                     18                   New Toronto         7   
20                     21                 Humber Summit         7   
21                     22                    Humbermede         7   
22                     23          Pelmo Park-Humberlea         7   
27                     28                        Rustic         7   
28                     29                    Maple Leaf         7   
29                     30           Brookhaven-Amesbury         7   
30                     31            Yorkdale-Glen Park         7   
32                     33                  Clanton Park         7   
33                     34                Bathurst Manor         7   
36                     37               Willowdale West         7   
42                     43              Victoria Village         7   
45                     46                 Pleasant View         7   
47                     48             Hillcrest Village         7   
48                     49         Bayview Woods-Steeles         7   
49                     50              Newtonbrook East         7   
52                     53                    Henry Farm         7   
53                     54             O'Connor-Parkview         7   
56                     57               Broadview North         7   
60                     61                 Taylor-Massey         7   
71                     72                   Regent Park         7   
73                     74           North St.James Town         7   
77                     78          Kensington-Chinatown         7   
90                     91            Weston-Pellam Park         7   
91                     92        Corso Italia-Davenport         7   
107                   108          Briar Hill-Belgravia         7   
108                   109            Caledonia-Fairbank         7   
109                   110      Keelesdale-Eglinton West         7   
111                   112       Beechborough-Greenbrook         7   
112                   113                        Weston         7   
114                   115                  Mount Dennis         7   
120                   121                      Oakridge         7   
122                   123                    Cliffcrest         7   
123                   124                  Kennedy Park         7   
124                   125                       Ionview         7   
133                   134                Highland Creek         7   
134                   135                   Morningside         7   
138                   139           Scarborough Village         7   

     Population, 2016  Average after-tax income of households in 2015 ($)  \
2               10360                                             140050    
3               10529                                             134305    
4                9456                                             123119    
7               10948                                             238655    
12              11848                                             132460    
17              11463                                             188819    
20              12416                                             202677    
21              15545                                             184459    
22              10722                                             154568    
27               9941                                             113995    
28              10111                                             144062    
29              17757                       

## Get Foursquare data

Define Foursquare Credentials and Version

In [58]:
CLIENT_ID = 'EKYLOJIRYVRFYUBRKVPLAY0BZEG52QPLCMH220LR21BJNT2H' # your Foursquare ID
CLIENT_SECRET = 'R0EB1FNJYG252UOG20URXWOJMGA5XFNK1XNOOZBGUEEFCSO2' # your Foursquare Secret
VERSION = '20190605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: EKYLOJIRYVRFYUBRKVPLAY0BZEG52QPLCMH220LR21BJNT2H
CLIENT_SECRET:R0EB1FNJYG252UOG20URXWOJMGA5XFNK1XNOOZBGUEEFCSO2


get_category_type function from the Foursquare lab.

In [59]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

A function to get the top 100 venues that are within a radius of 500 meters within the postcode's coordinates

In [79]:
LIMIT = 100

def getNearbyVenues(neighbourhood, latitudes, longitudes, radius=1000):
    
    venues_list=[]
    for neighbourhood, lat, lng in zip(neighbourhood, latitudes, longitudes):
        print(neighbourhood)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            neighbourhood, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

run the above function for each postcode and create a new dataframe called toronto_venues.

In [81]:
toronto_venues = getNearbyVenues(neighbourhood=df['Neighbourhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

West Humber-Clairville 
Mount Olive-Silverstone-Jamestown 
Thistletown-Beaumond Heights 
Rexdale-Kipling 
Elms-Old Rexdale 
Kingsview Village-The Westway 
Willowridge-Martingrove-Richview 
Humber Heights-Westmount 
Edenbridge-Humber Valley 
Princess-Rosethorn 
Eringate-Centennial-West Deane 
Markland Wood 
Etobicoke West Mall 
Islington-City Centre West 
Kingsway South 
Stonegate-Queensway 
Mimico (includes Humber Bay Shores) 
New Toronto 
Long Branch 
Alderwood 
Humber Summit 
Humbermede 
Pelmo Park-Humberlea 
Black Creek 
Glenfield-Jane Heights 
Downsview-Roding-CFB 
York University Heights 
Rustic 
Maple Leaf 
Brookhaven-Amesbury 
Yorkdale-Glen Park 
Englemount-Lawrence 
Clanton Park 
Bathurst Manor 
Westminster-Branson 
Newtonbrook West 
Willowdale West 
Lansing-Westgate 
Bedford Park-Nortown 
St.Andrew-Windfields 
Bridle Path-Sunnybrook-York Mills 
Banbury-Don Mills 
Victoria Village 
Flemingdon Park 
Parkwoods-Donalda 
Pleasant View 
Don Valley Village 
Hillcrest Village 
Bayview

In [82]:
toronto_venues.shape

(5704, 7)

In [83]:
toronto_venues.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  West Humber-Clairville                 43.71618               -79.596356   
1  West Humber-Clairville                 43.71618               -79.596356   
2  West Humber-Clairville                 43.71618               -79.596356   
3  West Humber-Clairville                 43.71618               -79.596356   
4  West Humber-Clairville                 43.71618               -79.596356   

                Venue  Venue Latitude  Venue Longitude  \
0            Fortinos       43.721582       -79.596233   
1     Mandarin Buffet       43.719798       -79.595820   
2         Tim Hortons       43.714657       -79.593716   
3  Woodbine Racetrack       43.715225       -79.604273   
4             Xawaash       43.715786       -79.593053   

             Venue Category  
0             Grocery Store  
1        Chinese Restaurant  
2               Coffee Shop  
3                Racecourse  
4  Mediterranean Restaurant

how many unique categories can be curated from all the returned venues

In [84]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 342 uniques categories.


how many venues were returned for each postcode

In [85]:
toronto_venues.groupby('Neighbourhood').count().head()

Neighbourhood Latitude  \
Neighbourhood                                           
Agincourt North                                    45   
Agincourt South-Malvern West                       37   
Alderwood                                          23   
Annex                                             100   
Banbury-Don Mills                                  46   

                               Neighbourhood Longitude  Venue  Venue Latitude  \
Neighbourhood                                                                   
Agincourt North                                     45     45              45   
Agincourt South-Malvern West                        37     37              37   
Alderwood                                           23     23              23   
Annex                                              100    100             100   
Banbury-Don Mills                                   46     46              46   

                               Venue Longitude  Venue Category  
Neighbourhood                                                   
Agincourt North                             45              45  
Agincourt South-Malvern West                37              37  
Alderwood                                   23              23  
Annex                                      100             100  
Banbury-Don Mills                           46              46

In [86]:
# one hot encoding
to_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

to_onehot.head()

Neighbourhood  ATM  Accessories Store  Afghan Restaurant  \
0  West Humber-Clairville     0                  0                  0   
1  West Humber-Clairville     0                  0                  0   
2  West Humber-Clairville     0                  0                  0   
3  West Humber-Clairville     0                  0                  0   
4  West Humber-Clairville     0                  0                  0   

   African Restaurant  American Restaurant  Amphitheater  Animal Shelter  \
0                   0                    0             0               0   
1                   0                    0             0               0   
2                   0                    0             0               0   
3                   0                    0             0               0   
4                   0                    0             0               0   

   Antique Shop  Arcade  ...  Vietnamese Restaurant  Warehouse Store  \
0             0       0  ...                      0                0   
1             0       0  ...                      0                0   
2             0       0  ...                      0                0   
3             0       0  ...                      0                0   
4             0       0  ...                      0                0   

   Whisky Bar  Wine Bar  Wine Shop  Wings Joint  Women's Store  Yoga Studio  \
0           0         0          0            0              0            0   
1           0         0          0            0              0            0   
2           0         0          0            0              0            0   
3           0         0          0            0              0            0   
4           0         0          0            0              0            0   

   Zoo  Zoo Exhibit  
0    0            0  
1    0            0  
2    0            0  
3    0            0  
4    0            0  

[5 rows x 343 columns]

examine the new dataframe size

In [87]:
to_onehot.shape

(5704, 343)

group by neighbourhood

In [88]:
to_grouped = to_onehot.groupby('Neighbourhood').mean().reset_index()
to_grouped

Neighbourhood  ATM  Accessories Store  \
0                      Agincourt North   0.0           0.000000   
1         Agincourt South-Malvern West   0.0           0.000000   
2                            Alderwood   0.0           0.000000   
3                                Annex   0.0           0.000000   
4                    Banbury-Don Mills   0.0           0.000000   
5                       Bathurst Manor   0.0           0.000000   
6                  Bay Street Corridor   0.0           0.000000   
7                      Bayview Village   0.0           0.000000   
8                Bayview Woods-Steeles   0.0           0.000000   
9                 Bedford Park-Nortown   0.0           0.000000   
10             Beechborough-Greenbrook   0.0           0.000000   
11                             Bendale   0.0           0.000000   
12               Birchcliffe-Cliffside   0.0           0.000000   
13                         Black Creek   0.0           0.000000   
14                         Blake-Jones   0.0           0.000000   
15                Briar Hill-Belgravia   0.0           0.000000   
16   Bridle Path-Sunnybrook-York Mills   0.0           0.000000   
17                     Broadview North   0.0           0.000000   
18                 Brookhaven-Amesbury   0.0           0.000000   
19     Cabbagetown-South St.James Town   0.0           0.000000   
20                  Caledonia-Fairbank   0.0           0.000000   
21                           Casa Loma   0.0           0.000000   
22              Centennial Scarborough   0.0           0.000000   
23               Church-Yonge Corridor   0.0           0.000000   
24                 Clairlea-Birchmount   0.0           0.000000   
25                        Clanton Park   0.0           0.000000   
26                          Cliffcrest   0.0           0.000000   
27              Corso Italia-Davenport   0.0           0.000000   
28                            Danforth   0.0           0.000000   
29                  Danforth East York   0.0           0.000000   
..                                  ...  ...                ...   
110                    South Riverdale   0.0           0.000000   
111               St.Andrew-Windfields   0.0           0.000000   
112                            Steeles   0.0           0.000000   
113                Stonegate-Queensway   0.0           0.000000   
114             Tam O'Shanter-Sullivan   0.0           0.000000   
115                      Taylor-Massey   0.0           0.000000   
116                        The Beaches   0.0           0.000000   
117       Thistletown-Beaumond Heights   0.0           0.000000   
118                   Thorncliffe Park   0.0           0.000000   
119                  Trinity-Bellwoods   0.0           0.000000   
120                         University   0.0           0.000000   
121                   Victoria Village   0.0           0.000000   
122  Waterfront Communities-The Island   0.0           0.000000   
123                          West Hill   0.0           0.000000   
124             West Humber-Clairville   0.0           0.000000   
125                Westminster-Branson   0.0           0.000000   
126                             Weston   0.0           0.000000   
127                 Weston-Pellam Park   0.0           0.000000   
128                   Wexford/Maryvale   0.0           0.000000   
129                    Willowdale East   0.0           0.000000   
130                    Willowdale West   0.0           0.000000   
131   Willowridge-Martingrove-Richview   0.0           0.000000   
132                             Woburn   0.0           0.000000   
133                  Woodbine Corridor   0.0           0.000000   
134                   Woodbine-Lumsden   0.0           0.000000   
135                           Wychwood   0.0           0.000000   
136                     Yonge-Eglinton   0.0           0.000000   
137                     Yonge-St.Clair   0.0           0.000000   
138   

In [90]:
to_grouped.shape

(140, 343)

a function to sort the venues in descending order.

In [91]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Create the new dataframe and display the top 10 venues for each postcode.

In [92]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
hoods_venues_sorted = pd.DataFrame(columns=columns)
hoods_venues_sorted['Neighbourhood'] = to_grouped['Neighbourhood']

for ind in np.arange(to_grouped.shape[0]):
    hoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(to_grouped.iloc[ind, :], num_top_venues)

hoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
0               Agincourt North     Chinese Restaurant                Bakery   
1  Agincourt South-Malvern West     Chinese Restaurant         Shopping Mall   
2                     Alderwood                   Park           Gas Station   
3                         Annex             Restaurant           Coffee Shop   
4             Banbury-Don Mills            Coffee Shop   Japanese Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0              Pharmacy         Shopping Mall           Pizza Place   
1  Cantonese Restaurant            Restaurant             Pool Hall   
2        Discount Store              Pharmacy           Pizza Place   
3                  Café                Bakery    Italian Restaurant   
4            Shoe Store            Restaurant        Clothing Store   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0           Supermarket           Coffee Shop  Vietnamese Restaurant   
1     Korean Restaurant      Sushi Restaurant            Supermarket   
2          Dance Studio                   Pub      Convenience Store   
3                   Pub     French Restaurant            Pizza Place   
4   American Restaurant                  Park                   Café   

           9th Most Common Venue 10th Most Common Venue  
0                 Sandwich Place      Indian Restaurant  
1                         Lounge         Breakfast Spot  
2     Construction & Landscaping           Intersection  
3  Vegetarian / Vegan Restaurant                 Museum  
4                   Burger Joint                 Bakery

In [112]:
df.sort_values('Neighbourhood',ascending=True, inplace=True)
df.reset_index(drop=False,inplace=True)

to_data_merged = pd.DataFrame
to_data_merged = pd.concat([df[['Neighbourhood Number','Cluster']],hoods_venues_sorted], axis=1)




In [113]:
to_data_merged

Neighbourhood Number  Cluster                       Neighbourhood  \
0                     129        0                    Agincourt North    
1                     128        0       Agincourt South-Malvern West    
2                      20        1                          Alderwood    
3                      95        2                              Annex    
4                      42        4                  Banbury-Don Mills    
5                      34        7                     Bathurst Manor    
6                      76        2                Bay Street Corridor    
7                      52        4                    Bayview Village    
8                      49        7              Bayview Woods-Steeles    
9                      39        4               Bedford Park-Nortown    
10                    112        7            Beechborough-Greenbrook    
11                    127        0                            Bendale    
12                    122        4              Birchcliffe-Cliffside    
13                     24        0                        Black Creek    
14                     69        1                        Blake-Jones    
15                    108        7               Briar Hill-Belgravia    
16                     41        1  Bridle Path-Sunnybrook-York Mills    
17                     57        7                    Broadview North    
18                     30        7                Brookhaven-Amesbury    
19                     71        1    Cabbagetown-South St.James Town    
20                    109        7                 Caledonia-Fairbank    
21                     96        1                          Casa Loma    
22                    133        1             Centennial Scarborough    
23                     75        2              Church-Yonge Corridor    
24                    120        0                Clairlea-Birchmount    
25                     33        7                       Clanton Park    
26                    123        7                         Cliffcrest    
27                     92        7             Corso Italia-Davenport    
28                     66        1                           Danforth    
29                     59        1                 Danforth East York    
..                    ...      ...                                 ...   
110                    70        4                    South Riverdale    
111                    40        1               St.Andrew-Windfields    
112                   116        0                            Steeles    
113                    16        4                Stonegate-Queensway    
114                   118        0             Tam O'Shanter-Sullivan    
115                    61        7                      Taylor-Massey    
116                    63        4                        The Beaches    
117                     3        7       Thistletown-Beaumond Heights    
118                    55        0                   Thorncliffe Park    
119                    81        1                  Trinity-Bellwoods    
120                    79        1                         University    
121                    43        7                   Victoria Village    
122                    77        6  Waterfront Communities-The Island    
123                   136        0                          West Hill    
124                     1        0             West Humber-Clairville    
125                    35        0                Westminster-Branson    
126                   113        7                             Weston    
127                    91        7                 Weston-Pellam Park    
128                   119        0                   Wexford/Maryvale    
129                    51        5                    Willowdale East    
130                    37        7                    Willowdale West    
131                     7        4   Willowridge-Martingrove-Richview    
132      

In [119]:
to_data_merged.loc[to_data_merged['Cluster'] == 0, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster      1st Most Common Venue  \
0                      Agincourt North         0         Chinese Restaurant   
1         Agincourt South-Malvern West         0         Chinese Restaurant   
11                             Bendale         0                       Park   
13                         Black Creek         0              Grocery Store   
24                 Clairlea-Birchmount         0                      Diner   
30                  Don Valley Village         0             Clothing Store   
31                         Dorset Park         0          Electronics Store   
33                Downsview-Roding-CFB         0                Supermarket   
37                       Eglinton East         0                Wings Joint   
42                     Flemingdon Park         0                Coffee Shop   
45              Glenfield-Jane Heights         0      Vietnamese Restaurant   
63       Kingsview Village-The Westway         0                Coffee Shop   
76                            Milliken         0         Chinese Restaurant   
81   Mount Olive-Silverstone-Jamestown         0                Coffee Shop   
86                    Newtonbrook West         0                       Park   
102                  Rockcliffe-Smythe         0                Pizza Place   
112                            Steeles         0         Chinese Restaurant   
114             Tam O'Shanter-Sullivan         0                Coffee Shop   
118                   Thorncliffe Park         0                Coffee Shop   
123                          West Hill         0                Pizza Place   
124             West Humber-Clairville         0                Coffee Shop   
125                Westminster-Branson         0                       Park   
128                   Wexford/Maryvale         0  Middle Eastern Restaurant   
138            York University Heights         0                Pizza Place   

    2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
0                  Bakery              Pharmacy           Shopping Mall   
1           Shopping Mall  Cantonese Restaurant              Restaurant   
11           Optical Shop    Chinese Restaurant           Grocery Store   
13     Chinese Restaurant    Athletics & Sports    Gym / Fitness Center   
24            Coffee Shop                Bakery                    Bank   
30                   Park  Fast Food Restaurant             Coffee Shop   
31   Fast Food Restaurant     Indian Restaurant    Gym / Fitness Center   
33         Baseball Field           Pizza Place   Vietnamese Restaurant   
37         Sandwich Place              Pharmacy    Fast Food Restaurant   
42    Japanese Restaurant         Grocery Store                    Café   
45   Gym / Fitness Center         Moving Target                Tea Room   
63            Pizza Place                  Bank         Supplement Shop   
76               Pharmacy                  Park    Cantonese Restaurant   
81          Grocery Store           Pizza Place            Liquor Store   
86               Wine Bar          Skating Rink             Zoo Exhibit   
102           Coffee Shop                  Park                    Bank   
112     Korean Restaurant              Tea Room       Food & Drink Shop   
114           Pizza Place              Pharmacy    Fast Food Restaurant   
118          Burger Joint         Shopping Mall  Furniture / Home Store   
123        Breakfast Spot           Coffee Shop    Fast Food Restaurant   
124                 Hotel           Pizza Place           Grocery Store   
125                Bakery              Pharmacy            Skating Rink   
128           Pizza Place          Intersection                  Bakery   
138           Coffee Shop           Frame Store          Massage Studio   

    5th Most Common Venue   6th Most Common Venue  \
0             Pizza Place             Supermarket   
1               Pool Hall       Korean Restaurant   
11            W

In [120]:
to_data_merged.loc[to_data_merged['Cluster'] == 1, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster 1st Most Common Venue  \
2                            Alderwood         1                  Park   
14                         Blake-Jones         1                  Café   
16   Bridle Path-Sunnybrook-York Mills         1                  Café   
19     Cabbagetown-South St.James Town         1                  Park   
21                           Casa Loma         1           Coffee Shop   
22              Centennial Scarborough         1                   Bar   
28                            Danforth         1                  Café   
29                  Danforth East York         1           Coffee Shop   
34                      Dufferin Grove         1                  Café   
36            Edenbridge-Humber Valley         1                  Park   
43                   Forest Hill North         1           Coffee Shop   
44                   Forest Hill South         1                  Park   
46                   Greenwood-Coxwell         1     Indian Restaurant   
47                           Guildwood         1                  Park   
56                  Humewood-Cedarvale         1           Pizza Place   
59                       Junction Area         1           Coffee Shop   
64                      Kingsway South         1           Coffee Shop   
66                  Lambton Baby Point         1                  Park   
67                    Lansing-Westgate         1                  Park   
68                 Lawrence Park North         1                Bakery   
69                 Lawrence Park South         1           Coffee Shop   
70                  Leaside-Bennington         1     Indian Restaurant   
71                     Little Portugal         1                   Bar   
72                         Long Branch         1           Coffee Shop   
75                       Markland Wood         1     Convenience Store   
82                 Mount Pleasant East         1           Coffee Shop   
88                     North Riverdale         1      Greek Restaurant   
93                       Old East York         1       Thai Restaurant   
94             Palmerston-Little Italy         1                  Café   
97            Playter Estates-Danforth         1      Greek Restaurant   
99                  Princess-Rosethorn         1        Clothing Store   
103                       Roncesvalles         1                Bakery   
106       Runnymede-Bloor West Village         1           Pizza Place   
111               St.Andrew-Windfields         1        Baseball Field   
119                  Trinity-Bellwoods         1                   Bar   
120                         University         1                  Café   
133                  Woodbine Corridor         1     Indian Restaurant   
134                   Woodbine-Lumsden         1                  Park   
135                           Wychwood         1           Coffee Shop   
136                     Yonge-Eglinton         1           Coffee Shop   
137                     Yonge-St.Clair         1           Coffee Shop   

             2nd Most Common Venue 3rd Most Common Venue  \
2                      Gas Station        Discount Store   
14                     Coffee Shop      Greek Restaurant   
16                     College Gym              Bus Line   
19                            Café             Pet Store   
21                  Sandwich Place                  Café   
22                            Pool            Playground   
28                     Coffee Shop                  Park   
29                            Café        Sandwich Place   
34                     Coffee Shop                   Bar   
36                          Bakery              Pharmacy   
43                     Pizza Place                  Bank   
44                            Café    Italian Restaurant   
46                            Café           Pizza Place   
47                   Grocery Store         Train Station   
56               

In [121]:
to_data_merged.loc[to_data_merged['Cluster'] == 2, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster 1st Most Common Venue  \
3                                 Annex         2            Restaurant   
6                   Bay Street Corridor         2           Coffee Shop   
23                Church-Yonge Corridor         2           Coffee Shop   
32  Dovercourt-Wallace Emerson-Junction         2                   Bar   
77  Mimico (includes Humber Bay Shores)         2              Pharmacy   
83                  Mount Pleasant West         2           Coffee Shop   
87                              Niagara         2           Coffee Shop   

   2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
3            Coffee Shop                  Café                  Bakery   
6                   Café   Japanese Restaurant          Clothing Store   
23        Clothing Store    Italian Restaurant     Japanese Restaurant   
32                  Café           Coffee Shop                  Bakery   
77     Convenience Store         Grocery Store       Indian Restaurant   
83    Italian Restaurant                  Café                     Gym   
87                  Café                  Park  Furniture / Home Store   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3       Italian Restaurant                   Pub     French Restaurant   
6       Italian Restaurant      Ramen Restaurant           Pizza Place   
23                 Theater      Ramen Restaurant                  Café   
32                Pharmacy                  Park    Mexican Restaurant   
77  Furniture / Home Store    Spanish Restaurant               Brewery   
83                    Park             Bookstore            Restaurant   
87                     Gym            Restaurant           Yoga Studio   

   8th Most Common Venue          9th Most Common Venue 10th Most Common Venue  
3            Pizza Place  Vegetarian / Vegan Restaurant                 Museum  
6    Arts & Crafts Store                 Breakfast Spot                Theater  
23           Pizza Place                     Restaurant         Sandwich Place  
32  Caribbean Restaurant                    Pizza Place                Brewery  
77        Breakfast Spot                 Sandwich Place            Coffee Shop  
83      Sushi Restaurant                      Gastropub           Dessert Shop  
87           Men's Store             Italian Restaurant            Music Venue

In [122]:
to_data_merged.loc[to_data_merged['Cluster'] == 3, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster 1st Most Common Venue  \
58   Islington-City Centre West         3           Coffee Shop   
65                   L'Amoreaux         3    Chinese Restaurant   
73                      Malvern         3           Pizza Place   
95            Parkwoods-Donalda         3                  Park   
105                       Rouge         3           Zoo Exhibit   
132                      Woburn         3              Pharmacy   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
58   Fast Food Restaurant         Grocery Store             Pet Store   
65   Fast Food Restaurant           Coffee Shop              Gym Pool   
73               Pharmacy                  Park                  Bank   
95     Chinese Restaurant  Fast Food Restaurant                  Road   
105                   Zoo  Fast Food Restaurant          Dessert Shop   
132           Coffee Shop     Indian Restaurant  Fast Food Restaurant   

     5th Most Common Venue          6th Most Common Venue  \
58                Pharmacy                 Sandwich Place   
65             Auto Garage                  Shopping Mall   
73    Fast Food Restaurant                 Sandwich Place   
95             Coffee Shop                  Train Station   
105              Gift Shop           Hungarian Restaurant   
132  Vietnamese Restaurant  Paper / Office Supplies Store   

    7th Most Common Venue  8th Most Common Venue 9th Most Common Venue  \
58            Pizza Place  Vietnamese Restaurant            Restaurant   
65         Breakfast Spot         Sandwich Place         Grocery Store   
73          Grocery Store                 Bakery    Salon / Barbershop   
95            Supermarket                   Café        Discount Store   
105     Fish & Chips Shop            Event Space    Falafel Restaurant   
132         Big Box Store         Discount Store                   Gym   

    10th Most Common Venue  
58           Shopping Mall  
65            Tennis Court  
73    Gym / Fitness Center  
95    Caribbean Restaurant  
105                   Farm  
132                   Park

In [123]:
to_data_merged.loc[to_data_merged['Cluster'] == 4, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster 1st Most Common Venue  \
4                   Banbury-Don Mills         4           Coffee Shop   
7                     Bayview Village         4                  Park   
9                Bedford Park-Nortown         4           Pizza Place   
12              Birchcliffe-Cliffside         4                  Park   
35                  East End-Danforth         4           Coffee Shop   
39                Englemount-Lawrence         4           Coffee Shop   
40     Eringate-Centennial-West Deane         4           Pizza Place   
49                    High Park North         4                   Bar   
50                  High Park-Swansea         4                  Park   
79                          Moss Park         4           Coffee Shop   
92                    Oakwood Village         4           Pizza Place   
104               Rosedale-Moore Park         4                  Park   
109                    South Parkdale         4                  Café   
110                   South Riverdale         4       Harbor / Marina   
113               Stonegate-Queensway         4    Italian Restaurant   
116                       The Beaches         4                   Pub   
131  Willowridge-Martingrove-Richview         4              Pharmacy   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
4     Japanese Restaurant            Shoe Store            Restaurant   
7             Coffee Shop  Outdoor Supply Store        Hardware Store   
9             Coffee Shop  Fast Food Restaurant    Italian Restaurant   
12                   Bank       College Stadium                   Gym   
35            Pizza Place              Bus Line         Grocery Store   
39                   Park  Fast Food Restaurant           Pizza Place   
40         Sandwich Place        Baseball Field     Convenience Store   
49            Coffee Shop                  Café           Pizza Place   
50            Coffee Shop         Deli / Bodega                Bakery   
79                   Café                  Park    Italian Restaurant   
92                   Park            Beer Store   Fried Chicken Joint   
104    Italian Restaurant                  Café           Pizza Place   
109                Bakery                   Bar    Tibetan Restaurant   
110         Moving Target    Athletics & Sports        Baseball Field   
113        Ice Cream Shop  Gym / Fitness Center                   Spa   
116           Coffee Shop                Bakery                  Park   
131          Liquor Store        Sandwich Place           Coffee Shop   

           5th Most Common Venue 6th Most Common Venue  \
4                 Clothing Store   American Restaurant   
7                     Shoe Store          Tennis Court   
9                     Bagel Shop      Sushi Restaurant   
12               Thai Restaurant              Gym Pool   
35              Sushi Restaurant        Ice Cream Shop   
39                    Restaurant            Bagel Shop   
40                          Park           Record Shop   
49                          Park       Thai Restaurant   
50            Light Rail Station           Flower Shop   
79                    Restaurant               Theater   
92                   Coffee Shop    Turkish Restaurant   
104                         Bank                   Spa   
109                         Park           Pizza Place   
110          Government Building                  Lake   
113  Eastern European Restaurant   Filipino Restaurant   
116               Breakfast Spot                 Beach   
131                  Pizza Place              Bus Line   

           7th Most Common Venue   8th Most Common Venue  \
4                           Park                    Café   
7                  Grocery Store          Clothing Store   
9                 Ice Cream Shop           Grocery Store   
12          Fast Food Restaurant   General Entertainment   
35                  Skating Rink          Sandwich

In [124]:
to_data_merged.loc[to_data_merged['Cluster'] == 5, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster 1st Most Common Venue 2nd Most Common Venue  \
129  Willowdale East         5           Coffee Shop           Pizza Place   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
129      Ramen Restaurant   Japanese Restaurant                  Café   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
129  Fast Food Restaurant              Pharmacy             Pet Store   

    9th Most Common Venue 10th Most Common Venue  
129      Sushi Restaurant             Restaurant

In [125]:
to_data_merged.loc[to_data_merged['Cluster'] == 6, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster 1st Most Common Venue  \
122  Waterfront Communities-The Island         6           Coffee Shop   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
122         Boat or Ferry           Pizza Place            Sports Bar   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
122                  Café           Music Venue            Steakhouse   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
122                 Hotel    Chinese Restaurant                    Gym

In [126]:
to_data_merged.loc[to_data_merged['Cluster'] == 7, to_data_merged.columns[[2] + [1] + list(range(3, to_data_merged.shape[1]))]]


Neighbourhood  Cluster      1st Most Common Venue  \
5                  Bathurst Manor         7                       Park   
8           Bayview Woods-Steeles         7                       Park   
10        Beechborough-Greenbrook         7             Sandwich Place   
15           Briar Hill-Belgravia         7     Furniture / Home Store   
17                Broadview North         7           Greek Restaurant   
18            Brookhaven-Amesbury         7      Portuguese Restaurant   
20             Caledonia-Fairbank         7                Coffee Shop   
25                   Clanton Park         7       Gym / Fitness Center   
26                     Cliffcrest         7             Discount Store   
27         Corso Italia-Davenport         7         Italian Restaurant   
38               Elms-Old Rexdale         7          Fish & Chips Shop   
41            Etobicoke West Mall         7          Convenience Store   
48                     Henry Farm         7                Coffee Shop   
51                 Highland Creek         7               Burger Joint   
52              Hillcrest Village         7             Sandwich Place   
53       Humber Heights-Westmount         7                Pizza Place   
54                  Humber Summit         7          Electronics Store   
55                     Humbermede         7      Vietnamese Restaurant   
57                        Ionview         7         Chinese Restaurant   
60       Keelesdale-Eglinton West         7                     Bakery   
61                   Kennedy Park         7                Coffee Shop   
62           Kensington-Chinatown         7                       Café   
74                     Maple Leaf         7                Coffee Shop   
78                    Morningside         7                Coffee Shop   
80                   Mount Dennis         7     Furniture / Home Store   
84                    New Toronto         7                Pizza Place   
85               Newtonbrook East         7  Middle Eastern Restaurant   
89            North St.James Town         7                Coffee Shop   
90              O'Connor-Parkview         7                    Brewery   
91                       Oakridge         7                       Bank   
96           Pelmo Park-Humberlea         7              Grocery Store   
98                  Pleasant View         7                       Park   
100                   Regent Park         7                Coffee Shop   
101               Rexdale-Kipling         7                Coffee Shop   
107                        Rustic         7      Vietnamese Restaurant   
108           Scarborough Village         7                Coffee Shop   
115                 Taylor-Massey         7                   Pharmacy   
117  Thistletown-Beaumond Heights         7          Indian Restaurant   
121              Victoria Village         7                Coffee Shop   
126                        Weston         7                Pizza Place   
127            Weston-Pellam Park         7         Italian Restaurant   
130               Willowdale West         7                       Park   
139            Yorkdale-Glen Park         7       Fast Food Restaurant   

             2nd Most Common Venue      3rd Most Common Venue  \
5                       Sports Bar             Breakfast Spot   
8                             Pool          Recreation Center   
10                    Dessert Shop     Furniture / Home Store   
15            Fast Food Restaurant                       Park   
17                          Bakery                       Café   
18                     Coffee Shop         Athletics & Sports   
20                        Pharmacy              Grocery Store   
25              Italian Restaurant       Other Great Outdoors   
26            Fast Food Restaurant                Coffee Shop   
27                            Café             Breakfast Spot   
38                   Grocery Store          Afgha

In [ ]:
toronto_geo = r'Neighbourhoods.json'

# create map and display it
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=12)
map_toronto.choropleth(
    geo_data=toronto_geo,
    data=df,
    columns=['Neighbourhood Number','Longitude'],
    key_on='feature.properties.AREA_LONG_CODE',
    fill_color='YlOrRd', 
    fill_opacity=0.6, 
    line_opacity=0.2,
    legend_name='Toronto Neighbourhood')
# display the map of Toronto
map_toronto